# Sravni

In [24]:
import requests
import time
import math
from tqdm import tqdm  # прогресс бар


import random
import logging

In [25]:
BASE_URL = "https://www.sravni.ru/proxy-reviews/reviews"
HEADERS = {"User-Agent": "Mozilla/5.0"}
FILTER_BY = "all"
PAGE_SIZE = 500
REVIEW_OBJECT_ID = "5bb4f768245bc22a520a6115"
REVIEW_OBJECT_TYPE = "banks"
TAGS = [
    "debitCards", "serviceLevel", "creditCards",
    "credits", 'savings', 'mortgage',
    'autocredits', 'creditRefinancing', 'mortgageRefinancing',
    'currencyExchange', 'usloviya', 'moneyOrder',
    'mobilnoyeprilozheniye', 'businessRko', 'acquiring',
    'remoteService', 'other'
]  # сюда можно добавить все теги
SLEEP_BETWEEN_REQUESTS = (0.5, 1.5)  # диапазон случайной задержки между запросами в секундах

In [30]:
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

all_reviews = {}

for tag in TAGS:
    logging.info(f"Начинаем парсинг для тега: {tag}")
    
    params = {
        "FilterBy": FILTER_BY,
        "LocationGarId": "",
        "NewIds": "true",
        "OrderBy": "byPopularity",
        "PageIndex": 1,  # первая страница
        "PageSize": PAGE_SIZE,
        "ReviewObjectId": REVIEW_OBJECT_ID,
        "ReviewObjectType": REVIEW_OBJECT_TYPE,
        "SpecificProductId": "",  
        "SqueezesVectorIds": "",
        "Tag": tag,
        "WithVotes": "true",
        "fingerPrint": "4e34dd05c0d5f23b5e4feb3ece2d3cfd"
    }
    
    response = requests.get(BASE_URL, params=params, headers=HEADERS)
    data = response.json()
    
    total_reviews = data.get("total", 0)
    total_pages = math.ceil(total_reviews / PAGE_SIZE)
    logging.info(f"TAG: {tag}")
    logging.info(f"Всего отзывов: {total_reviews}, страниц: {total_pages}")
    
    tag_reviews = []
    
    for page in tqdm(range(total_pages), desc=f"Парсинг {tag}", unit="стр"):
        params["PageIndex"] = page
        try:
            resp = requests.get(BASE_URL, params=params, headers=HEADERS)
            page_data = resp.json()
            
            items = page_data.get("items", [])
            for item in items:
                tag_reviews.append({
                    "id": item.get("id"),
                    "date": item.get("date"),
                    "title": item.get("title"),
                    "text": item.get("text"),
                    "specificProductName": item.get("specificProductName")
                })
            
            time.sleep(random.uniform(*SLEEP_BETWEEN_REQUESTS))
        
        except Exception as e:
            logging.error(f"Ошибка на странице {page} тега {tag}: {e}")
            time.sleep(2)
    
    all_reviews[tag] = tag_reviews
    logging.info(f"Собрано {len(tag_reviews)} отзывов для тега {tag}")

logging.info("Парсинг завершен!")

2025-09-20 21:05:04,297 - INFO - Начинаем парсинг для тега: debitCards
2025-09-20 21:05:04,637 - INFO - TAG: debitCards
2025-09-20 21:05:04,638 - INFO - Всего отзывов: 1147, страниц: 3
Парсинг debitCards: 100%|██████████| 3/3 [00:05<00:00,  1.99s/стр]
2025-09-20 21:05:10,604 - INFO - Собрано 1147 отзывов для тега debitCards
2025-09-20 21:05:10,604 - INFO - Начинаем парсинг для тега: serviceLevel
2025-09-20 21:05:11,461 - INFO - TAG: serviceLevel
2025-09-20 21:05:11,462 - INFO - Всего отзывов: 708, страниц: 2
Парсинг serviceLevel: 100%|██████████| 2/2 [00:04<00:00,  2.16s/стр]
2025-09-20 21:05:15,790 - INFO - Собрано 708 отзывов для тега serviceLevel
2025-09-20 21:05:15,790 - INFO - Начинаем парсинг для тега: creditCards
2025-09-20 21:05:16,388 - INFO - TAG: creditCards
2025-09-20 21:05:16,390 - INFO - Всего отзывов: 609, страниц: 2
Парсинг creditCards: 100%|██████████| 2/2 [00:03<00:00,  1.92s/стр]
2025-09-20 21:05:20,228 - INFO - Собрано 609 отзывов для тега creditCards
2025-09-20 21:

In [31]:
all_reviews

{'debitCards': [{'id': 992651,
   'date': '2025-08-29T23:30:38.746003Z',
   'title': 'Не\xa0выполняют условия акции!',
   'text': 'В\xa0апреле 2025 года я\xa0рекомендовала дебетовую карту другу согласно акции банка «Приведи друга». Далее в\xa0мае и\xa0мною и\xa0другом условия были выполнены, но\xa0вознаграждение по\xa0акции пришло другу только 9\xa0июля 2025, а\xa0мне не\xa0пришло совсем. Начиная с\xa0июня много раз писала в\xa0чат поддержки банка, но\xa0каждый раз получала стандартные отписки от\xa0операторов, что необходимо ждать, и\xa0в\xa0итоге после долгих мучений другу выплатили вознаграждение 9\xa0июля 2025, как писала ранее. И\xa0вот, 15\xa0июля 2025 я\xa0снова написала в\xa0чат поддержки банка с\xa0вопросом почему другу в\xa0конце концов пришло вознаграждение, а\xa0мне нет, позвала оператора в\xa012:17, в\xa012:30 подключился оператор Сергей, попросил 4 цифры телефона друга и\xa0сразу отключился, при том что я\xa0написала ответ в\xa0эту\xa0же минуту. Следующий оператор Татьяна

In [33]:
import pandas as pd

# Создаем пустой список, в который будем собирать все отзывы с тегами
all_records = []

for tag, reviews in all_reviews.items():
    for review in reviews:
        review_copy = review.copy()  # чтобы не менять оригинальный словарь
        review_copy["tag"] = tag     # добавляем колонку с тегом
        all_records.append(review_copy)

# Создаем DataFrame
df = pd.DataFrame(all_records)


In [36]:
df.to_csv('../data/sravni_reviews.csv')

In [37]:
df_ = pd.read_csv('../data/sravni_reviews.csv')

In [21]:
import requests

url = "https://www.sravni.ru/proxy-reviews/reviews"

params = {
    "FilterBy": "all",
    "LocationGarId": "",
    "NewIds": "true",
    "OrderBy": "byPopularity",
    "PageIndex": 1,  # Начнем с первой страницы
    "PageSize": 500,
    "ReviewObjectId": "5bb4f768245bc22a520a6115",
    "ReviewObjectType": "banks",
    "SpecificProductId": "",
    "SqueezesVectorIds": "",
    "Tag": "debitCards",
    "WithVotes": "true",
    "fingerPrint": "4e34dd05c0d5f23b5e4feb3ece2d3cfd"
}

headers = {
    "User-Agent": "Mozilla/5.0"
}

response = requests.get(url, params=params, headers=headers)
data = response.json()

# Проверим структуру
print(data.keys())
print(len(data.get("items", [])))  # Количество отзывов на странице
print(data["items"][0])  # Первый отзыв

dict_keys(['averageRating', 'items', 'pageIndex', 'pageSize', 'total'])
500
{'commentsCount': 0, 'id': 852338, 'userId': 32595530, 'date': '2024-10-04T08:14:16.398934Z', 'locationId': 83, 'locationGarId': 1405113, 'title': 'Не\xa0вернули кешбек', 'text': 'Заказывал карту Юнион Пей за 5 тысяч рублей. Надеялся по условиям вернуть их, но отказали. Т. К. В первый день (в день выдачи карты не было остатка в 50 тысяч рублей). Карту привез курьер, вместе с ним зайти и пополнить не смогли. Посоветовал сделать это через 2 часа самому. Не получилось. Смог пополнить только на следующий день. В течение 4 месяцев узнавал, выполняются ли условия по возврату комисси за выпуск. Ответить ничего не могли — ждите. Ужасный сервис. Никогда никому не порекомендую этот банк. Сейчас звонят: оформите привилегии, кредиты, ничего не хочу. Нет уверенности, что этот банк не спишет скрытых комиссий. Обходите этот банк стороной.', 'reviewObjectId': '5bb4f768245bc22a520a6115', 'reviewObjectType': 'banks', 'reviewTag'

In [15]:
data["total"]

1147

In [16]:
data["items"]

[{'commentsCount': 2,
  'id': 375100,
  'userId': 6584174,
  'date': '2020-08-11T10:44:08.49Z',
  'locationId': 847,
  'locationGarId': 454846,
  'title': 'Неудачное занесение денежных средств на карту',
  'text': '08.07.2020 года, вносил 10000 рублей через банкомат № 467696, расположенный в отделении Газпромбанка по ул.Савушкина 25, в городе Астрахань.\n\nБанкомат деньги взял, но зачисленными на счет они не стали.\n\nБанкомат выдал чек в котором было отображено что внесено 10000 рублей и так же еще одна запись, что транзакция не может быть выполнена.\n\nТут же обратился с заявлением о неуспешной операции в банкомате в это отделение  Газпромбанка, где приложил копию чека к заявлению.\n\nСпециалист банка объяснила, что  рассмотр проишествия проходит в течении 30 дней.\n\nТак же, в этот день я позвонил на горячую линию Газпромбанка, где приняв мое заявление, сказали что, так же будет рассмотр заявления и возрат денег в течении 30 дней. Так же мне сказали , что этот банкомат не исправен  

In [22]:
len(data["items"])

500

# Banki.ru

In [47]:
import requests
import time
import logging
from tqdm import tqdm

In [48]:
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s [%(levelname)s] %(message)s",
    handlers=[logging.StreamHandler()]
)

In [87]:
BASE_URL = "https://www.banki.ru/services/responses/list/ajax/"
HEADERS = {"User-Agent": "Mozilla/5.0"}

PRODUCTS = [
    "debitcards", "creditcards", "hypothec", "autocredits", "credits", "restructing",
    "deposits", "transfers", "remote", "other", "mobile_app", "individual", "rko",
    "acquiring", "salary_project", "businessdeposits", "businesscredits", "bank_guarantee",
    "leasing", "business_other", "business_remote", "business_mobile_app", "legal"
]

In [88]:
def parse_product(product, bank="gazprombank", sleep_time=1.2):
    page = 1
    reviews = []

    logging.info(f"Начинаем парсинг продукта: {product}")

    while True:
        params = {
            "page": page,
            "product": product,
            "type": "all",
            "bank": bank
        }

        try:
            response = requests.get(BASE_URL, params=params, headers=HEADERS, timeout=10)
            response.raise_for_status()
            data = response.json()
        except Exception as e:
            logging.error(f"Ошибка при запросе {product}, страница {page}: {e}")
            break

        items = data.get("data", [])
        if len(items) == 0:  # <-- условие выхода
            logging.info(f"Отзывы по продукту {product} закончились на странице {page-1}")
            break

        for item in items:
            reviews.append({
                "id": item.get("id"),
                "title": item.get("title"),
                "text": item.get("text"),
                "grade": item.get("grade"),
                "agentAnswerText": item.get("agentAnswerText"),
                'dateCreate': item.get('dateCreate')
            })

        if page % 10 == 0:
            logging.info(f"{product}: собрано {len(reviews)} отзывов (страница {page})")

        page += 1
        time.sleep(sleep_time)  # чтобы не забанили

    return reviews

In [89]:
def parse_all_products(products_list=PRODUCTS, bank="gazprombank"):
    all_reviews = {}

    for product in tqdm(products_list, desc="Парсинг продуктов"):
        product_reviews = parse_product(product, bank)
        all_reviews[product] = product_reviews
        logging.info(f"{product}: всего собрано {len(product_reviews)} отзывов")

    return all_reviews

In [90]:
all_reviews_new_v2 = parse_all_products()


Парсинг продуктов:   0%|          | 0/23 [00:00<?, ?it/s]2025-09-22 21:04:09,885 - INFO - Начинаем парсинг продукта: debitcards
2025-09-22 21:04:28,100 - INFO - debitcards: собрано 250 отзывов (страница 10)
2025-09-22 21:04:45,774 - INFO - debitcards: собрано 500 отзывов (страница 20)
2025-09-22 21:05:03,590 - INFO - debitcards: собрано 750 отзывов (страница 30)
2025-09-22 21:05:22,304 - INFO - debitcards: собрано 1000 отзывов (страница 40)
2025-09-22 21:05:41,603 - INFO - debitcards: собрано 1250 отзывов (страница 50)
2025-09-22 21:06:00,724 - INFO - debitcards: собрано 1500 отзывов (страница 60)
2025-09-22 21:06:20,327 - INFO - debitcards: собрано 1750 отзывов (страница 70)
2025-09-22 21:06:40,500 - INFO - debitcards: собрано 2000 отзывов (страница 80)
2025-09-22 21:06:59,686 - INFO - debitcards: собрано 2250 отзывов (страница 90)
2025-09-22 21:07:18,889 - INFO - debitcards: собрано 2500 отзывов (страница 100)
2025-09-22 21:07:38,562 - INFO - debitcards: собрано 2750 отзывов (страниц

In [58]:
all_reviews.keys()

dict_keys(['debitCards', 'serviceLevel', 'creditCards', 'credits', 'savings', 'mortgage', 'autocredits', 'creditRefinancing', 'mortgageRefinancing', 'currencyExchange', 'usloviya', 'moneyOrder', 'mobilnoyeprilozheniye', 'businessRko', 'acquiring', 'remoteService', 'other'])

In [73]:
len(all_reviews['usloviya'])

3

In [66]:
all_reviews['savings']

[{'id': 998516,
  'date': '2025-09-15T16:31:54.764937Z',
  'title': 'Газпромбанк обманул\xa0навязали дополнительную услугу доверительное управление ценными бумагами.',
  'text': 'Производил оформление открытия срочного банковского вклада «Стратегия успеха».\xa0В\xa0мне была навязана дополнительная услуга доверительное управление ценными бумагами и\xa0предложено внести в\xa0банк 500000 рублей. При этом меня уверили (наврали) что через пол года при окончании вклада я\xa0100% смогу забрать 500000 рублей даже с\xa0процентами. При этом сотрудница вошла в\xa0мое доверие и\xa0пользуясь моей финансовой безграмотностью и\xa0намеренно ввела меня в\xa0заблуждение. Так мне не\xa0было разъяснено, что при закрытии данного банковского продукта с\xa0меня удержат комиссию и\xa0какие риски могут быть при закрытии. И\xa0что закрыть я\xa0его через пол года не\xa0смогу снять.\n\nПри этом мне подсовывали много документов на\xa0подпись уверяя что все там нормально. Более этого мне отдали не\xa0все оригиналы 

In [91]:
import pandas as pd

# all_reviews у тебя получается после работы парсера
# формат: {"debitcards": [ {...}, {...} ], "creditcards": [ {...}, ...], ...}

all_records = []

for product, reviews in all_reviews_new_v2.items():
    for review in reviews:
        review_copy = review.copy()   # копия словаря, чтобы не затронуть оригинал
        review_copy["product"] = product  # добавляем колонку "product"
        all_records.append(review_copy)

# Превращаем всё в DataFrame
df_all_reviews_new_banki = pd.DataFrame(all_records)



In [92]:
df_all_reviews_new_banki

id                                              title  \
0      12567677                                  Развод со ставкой   
1      12567381  Банкомат не выдал наличные, а деньги списал со...   
2      12567376             Оформление карты по реферальной ссылке   
3      12567253                Получение дебетовой карты ульяновск   
4      12567156                          Получение дебетовой карты   
...         ...                                                ...   
45831  11323939                          Обман и навязывание услуг   
45832  11321849                                        Дикий запад   
45833  11282806                                            Депозит   
45834  11266609               Наплевательское отношение к клиентам   
45835  11219233  Хороший отзыв к Газпромбанк(у) от Чиновник(а) ...   

                                                    text  grade  \
0      <p>Ради безопасности решил часть средств вложи...    2.0   
1      <p>Сегодня, 22 сентяюря 2025 года в 12-55 (Сар...    2.0   
2      <p>Оформил заказ на дебетовую карту дочери по ...    3.0   
3      <p>Хочу поблагодарить представителя Ксению, по...    5.0   
4      <p>Здравствуйте. <br>Заказала карту Газпромбан...    5.0   
...                                                  ...    ...   
45831  Добрый вечер Уважаемое руководство банка!\r\nС...    1.0   
45832  <p>Карточный счёт по не действующей, неактивно...    1.0   
45833  Я являюсь клиентом Газпромбанк несколько лет. ...    5.0   
45834  Оформила онлайн-заявку на получение дебетовой ...    1.0   
45835  <p>Грамотные услуги и внутренних систем работы...    5.0   

                                         agentAnswerText           dateCreate  \
0                                                   None  2025-09-22 20:37:22   
1                                                   None  2025-09-22 17:37:05   
2                                                   None  2025-09-22 17:34:14   
3      Здравствуйте!\n\nБлагодарим за положительный о...  2025-09-22 16:37:28   
4      Здравствуйте!\n\nБлагодарим за высокую оценку....  2025-09-22 15:54:51   
...                                                  ...                  ...   
45831  Здравствуйте!\r\n\r\nВаше обращение принято в ...  2024-01-10 22:17:28   
45832  Здравствуйте!\r\n\r\nВаше обращение принято в ...  2024-01-09 17:14:53   
45833  Здравствуйте!\r\n\r\nМы рады, что вы выбрали н...  2023-12-15 22:14:57   
45834  Здравствуйте!\r\n\r\nНам жаль, что сложилась т...  2023-12-10 10:05:20   
45835  Здравствуйте! \r\n\r\nСпасибо за положительный...  2023-11-21 16:58:45   

                product  
0            debitcards  
1            debitcards  
2            debitcards  
3            debitcards  
4            debitcards  
...                 ...  
45831  businessdeposits  
45832  businessdeposits  
45833  businessdeposits  
45834  businessdeposits  
45835  businessdeposits  

[45836 rows x 7 columns]

In [93]:
df_all_reviews_new_banki.to_csv('banki_reviews_v2.csv')

In [84]:
len(df_all_reviews_new_banki[['title', 'text']].unique())

AttributeError: 'DataFrame' object has no attribute 'unique'

In [45]:
import requests

url = "https://www.banki.ru/services/responses/list/ajax/"

params = {
    "page": 22222,               # Номер страницы
    "product": "debitcards", # Тип продукта
    "type": "all",           # Тип отзывов
    "bank": "gazprombank"    # Банк
}

headers = {
    "User-Agent": "Mozilla/5.0"
}

response = requests.get(url, params=params, headers=headers)
data = response.json()

print(data.keys())  # Проверим, какие ключи есть


dict_keys(['data', 'hasMorePages'])


In [46]:
len(data['data'])

0

In [44]:
data['data']

[{'id': 12561858,
  'title': 'Компетентность сотрудника',
  'userName': 'user-593022833415',
  'text': '<ul>\r\n<li>Сегодня получала новую дебетовую карту. Очень довольна компетентностью сотрудника банка. Приём прошёл точно по времени. Я получила ответы на все мои вопросы. А их было немало. Терпеливо и грамотно мне все разъяснили. Были даны советы как лучше пользоваться картой, какие у карты преимущества. Благодарю!\xa0</li>\r\n</ul>',
  'grade': 5,
  'commentCount': 0,
  'isCountable': None,
  'dateCreate': '2025-09-19 13:06:02',
  'resolutionIsApproved': None,
  'agentAnswerText': 'Здравствуйте!\n\nМы рады, что вы выбрали наш банк в качестве финансового партнера.\nБудем признательны, если вы расскажете о консультации подробнее. Например, когда состоялась встреча? Сколько времени заняла консультация? \nЭта информация будет полезна администраторам портала при принятии решения о зачете отзыва.\n\nС уважением,\nКоманда экспертов Газпромбанка\n',
  'agentId': 2764,
  'company': {'id': 276

In [39]:
import json

response_text = r"""\u0421\u043f\u0438\u0441\u0430\u043d\u0438\u0435 \u0431\u0430\u043b\u043b\u043e\u0432 \u043a\u0435\u0448\u0431\u0435\u043a\u0430 \u0431\u0435\u0437 \u0438\u043d\u0444\u043e\u0440\u043c\u0438\u0440\u043e\u0432\u0430\u043d\u0438\u044f \u043a\u043b\u0438\u0435\u043d\u0442\u0430."""
decoded_text = json.loads(f'"{response_text}"')  # Декодирует Unicode и экранирование
print(decoded_text)


Списание баллов кешбека без информирования клиента.
